# Unternehmensregister

## Fetch Auszug

In [74]:
import os
from pathlib import Path

from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC

search_query = "A*"

options = webdriver.ChromeOptions()

download_path = str(Path(Path.cwd() / "data" / "Unternehmensregister"))
print(download_path)

preferences = {
    "profile.default_content_settings.popups": 0,
    "safebrowsing.enabled": True,
    "download": {
        "directory_upgrade": True,
        "prompt_for_download": False,
        "extensions_to_open": "",
        "default_directory": download_path,
    },
}
options.add_experimental_option("prefs", preferences)

driver = webdriver.Chrome(options=options)

driver.get("https://www.unternehmensregister.de/ureg/")
# Accept Cookies
driver.find_elements(
    By.XPATH, '//button[text()="Nur technisch notwendige Cookies akzeptieren"]'
)[0].click()
# Enter search query
driver.find_elements(By.ID, "globalSearchForm:extendedResearchCompanyName")[
    0
].send_keys(search_query)
# Trigger search
driver.find_elements(By.ID, "globalSearchForm:btnExecuteSearchOld")[0].click()
# Wait for results
wait = WebDriverWait(driver, 5)
wait.until(
    lambda driver: driver.current_url != "https://www.unternehmensregister.de/ureg/"
)
## TODO Iterate over tabs
# Find all "Registerinformationen"
companies_tab = driver.find_elements(
    By.LINK_TEXT, "Registerinformationen des Registergerichts"
)
for company_link in companies_tab:
    # Go to intermediary page
    company_link.click()
    # Trigger next redirect
    driver.find_element(By.LINK_TEXT, "Registerinformationen anzeigen").click()
    # Trigger SI download
    driver.find_element(By.LINK_TEXT, "SI").click()
    # Show shopping cart - TODO evaluate restructuring behaviour by filling cart first and then bulk downloading
    wait.until(
        EC.visibility_of_element_located((By.LINK_TEXT, "Dokumentenkorb ansehen"))
    )
    driver.find_element(By.LINK_TEXT, "Dokumentenkorb ansehen").click()
    # Get document
    xpath = "//input[@type='submit']"
    elems = driver.find_elements(By.TAG_NAME, "input")
    elems[-2].click()

    driver.find_element(By.ID, "paymentFormOverview:btnNext").click()
    driver.find_element(By.LINK_TEXT, "Zum Dokumentenkorb").click()
    driver.find_element(By.CLASS_NAME, "download-wrapper").click()

    for i in range(6):
        driver.back()

driver.close()

c:\Users\trist\Documents\Code\M.Sc\aki_prj23_transparenzregister\Jupyter\API-tests\Unternehmensregister\data\Unternehmensregister


In [ ]:
import re
import requests

session = requests.Session()
session.cookies["cc"] = "1686301974-69f11760d466bcea-10"
session.headers.update(
    {
        "Accept": "text/html,application/xhtml+xml,application/xml;q=0.9,image/avif,image/webp,image/apng,*/*;q=0.8,application/signed-exchange;v=b3;q=0.9",
        "Accept-Encoding": "gzip, deflate, br",
        "Accept-Language": "de-DE,de;q=0.9,en-US;q=0.8,en;q=0.7,et;q=0.6,pl;q=0.5",
        "Cache-Control": "max-age=0",
        "Connection": "keep-alive",
        "DNT": "1",
        "Host": "www.unternehmensregister.de",
        "Pragma": "no-cache",
        "Referer": "https://www.unternehmensregister.de/ureg/",
        "sec-ch-ua-mobile": "?0",
        "Sec-Fetch-Dest": "document",
        "Sec-Fetch-Mode": "navigate",
        "Sec-Fetch-Site": "same-origin",
        "Sec-Fetch-User": "?1",
        "Upgrade-Insecure-Requests": "1",
        "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/92.0.4515.131 Safari/537.36",
        "Content-Type": "application/x-www-form-urlencoded",
    }
)


# Get session cookie
response = session.get("https://www.unternehmensregister.de")
jsessionid = re.findall(r";jsessionid=[A-Z0-9]*.web[0-9]{2}.[0-9]", response.text)[
    0
].replace(";jsessionid=", "")
print(jsessionid)
with open("temp.html", "w", encoding="utf-8") as file:
    file.write(response.text)
print(session.cookies)
# Go to search page
response = session.get("https://www.unternehmensregister.de/ureg/")
# Start search
response = session.post(
    f"https://www.unternehmensregister.de/ureg/index.html;jsessionid={jsessionid}",
    data={
        "globalSearchForm": "globalSearchForm",
        "globalSearchForm:extendedResearchCompanyName": "A*",
    },
)
print(response.status_code)
# Get results
response = session.get(
    f"https://www.unternehmensregister.de/ureg/result.html;jsessionid={jsessionid}"
)
with open("temp.html", "w", encoding="utf-8") as file:
    file.write(response.text)

print(session.cookies)

In [ ]:
class Unternehmensregister:
    def __init__(self):
        self.session = requests.Session()

## Analyze Auszug

In [27]:
from pdf2image import convert_from_path

pdfs = r"./data/test.pdf"
pages = convert_from_path(pdfs, 350)


for i, page in enumerate(pages):
    image_name = f"./data/Page_{i+1}.jpg"
    page.save(image_name, "JPEG")

In [28]:
import cv2
import pytesseract

image_path = "./data/Page_1.jpg"
image = cv2.imread(image_path)

text = str(pytesseract.image_to_string(image, config="--psm 6", lang="deu"))
print(text)
with open("./data/Page_1.txt", "w", encoding="utf-8") as output_file:
    output_file.write(text)

Handelsregister B des Abteilung B Nummer der Firma:
Amtsgerichts Hamm Wiedergabe des aktuellen HRB 5363
Registerinhalts
Abruf vom 07.06.2023 19:37
1. Anzahl der bisherigen Eintragungen:
51
2. a) Firma:
GEA Farm Technologies GmbH
b) Sitz, Niederlassung, inländische Geschäftsanschrift, empfangsberechtigte Person, Zweigniederlassungen:
Bönen
Geschäftsanschrift: Siemensstraße 25-27, 59199 Bönen
c) Gegenstand des Unternehmens:
Entwicklung, Herstellung und der Vertrieb von Landtechnik, insbesondere von Komponenten und Anlagen
(a) zur Gewinnung, Kühlung, Behandlung und Lagerung von Milch;
(b) für das Milchvieh-Herdenmanagement;
(c) zur Tierhygiene und Sicherung der Milchqualität und
(d) zur Aufstallung von Tieren;
sowie die Herstellung und der Vertrieb von Anlagen und Fahrzeugen zur Aufbereitung und zum Transport von Gülle.
3. Grund- oder Stammkapital:
5.115.000,00 EUR
4. a) Allgemeine Vertretungsregelung:
Ist nur ein Geschäftsführer bestellt, so vertritt er die Gesellschaft allein. Sind mehr

In [29]:
import re


def get_managing_directors(text: str) -> list:
    managing_directors_regex = r"Geschäftsführer: [a-zA-ZäöüÄÖÜ]*, [a-zA-ZäöüÄÖÜ]*"
    hits = re.findall(managing_directors_regex, text)
    print(hits)
    return [
        " ".join(hit.replace("Geschäftsführer: ", "").replace(",", "").split(" ")[::-1])
        for hit in hits
    ]


get_managing_directors(text)

['Geschäftsführer: Basaran, Erkul', 'Geschäftsführer: Cheng, Liang', 'Geschäftsführer: Lauwers, Peter']


['Erkul Basaran', 'Liang Cheng', 'Peter Lauwers']